In [34]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np

plt.rcParams.update({'font.size': 20})
title_font_size = 27


In [20]:
WORK_DIR = "../../src/results/deepglobe/"
WORK_DIR2 = "../../src/results/deepglobe/CbMLC/"

WORK_DIR = "/home/joking/Downloads/results/deepglobe/lamp/"
WORK_DIR2 = "/home/joking/Downloads/results/deepglobe/resnet_base/"

CSV_LIST = ["train_results.csv", "valid_results.csv", "test_results.csv", "losses.csv"]
models = ["resnet_base"]#, "CbMLC", "lamp", ]


In [21]:
def plot_df(model_dir, title ="model"):

    # list of model folders with results in it
    # for example 11.07_09.41_.glove_d_300.epochs_50.loss_weighted_bce.sgd.lr_005
    l = [elem for elem in os.listdir(model_dir) if not elem.startswith('.')]
    n_cols = 3
    n_rows=len(l)
    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*7), dpi=300)

    for i, elem in enumerate(l):
        fig.suptitle(title)
        path=dir+elem+'/results.csv'
        df = pd.read_csv(path)

        axs[i,0].plot(df['epoch'], df['train_maAP']*100, label='train_maAP', linestyle='dotted', c='r')
        axs[i,0].plot(df['epoch'], df['train_miAP']*100, label='train_miAP', linestyle='dotted', c='b')
        axs[i,0].plot(df['epoch'], df['valid_maAP']*100, label='valid_maAP', linestyle='solid', c='r')
        axs[i,0].plot(df['epoch'], df['valid_miAP']*100, label='valid_miAP', linestyle='solid', c='b')

        axs[i,0].set_title(f'{elem}')
        axs[i,0].set_xlabel('epochs')
        axs[i,0].set_ylabel('Metric')
        axs[i,0].grid(axis="x")
        axs[i,0].grid(axis="y")
        axs[i,0].yaxis.set_ticks(np.arange(0,101,10))

        legend = axs[i,0].legend(loc='lower right', shadow=True, fontsize='x-large')


        axs[i,1].plot(df['epoch'], df['train_maF1']*100, label='train_maF1', linestyle='dotted', c='r')
        axs[i,1].plot(df['epoch'], df['train_miF1']*100, label='train_miF1', linestyle='dotted', c='b')
        axs[i,1].plot(df['epoch'], df['valid_maF1']*100, label='valid_maF1', linestyle='solid', c='r')
        axs[i,1].plot(df['epoch'], df['valid_miF1']*100, label='valid_miF1', linestyle='solid', c='b')

        axs[i,1].set_title(f'F1: {elem}')
        axs[i,1].set_xlabel('epochs')
        axs[i,1].set_ylabel('Metrics')
        axs[i,1].grid(axis="x")
        axs[i,1].grid(axis="y")
        axs[i,1].yaxis.set_ticks(np.arange(0,101,10))
        legend = axs[i,1].legend(loc='lower right', shadow=True, fontsize='x-large')

        
        axs[i,2].plot(df['epoch'], df['train_loss']*100, label='train loss', linestyle='dotted', c = 'r')
        axs[i,2].plot(df['epoch'], df['train_loss']*100, label='valid loss', linestyle='solid', c = 'b')
        max_loss = (max(df['train_loss'].max(), df['valid_loss'].max()))

        
        axs[i,2].set_title(f'Loss: {elem}')
        axs[i,2].set_xlabel('epochs')
        axs[i,2].set_ylabel('loss')
        axs[i,1].yaxis.set_ticks(np.arange(0,max_loss+1,max_loss/10))
        axs[i,2].grid(axis="x")
        axs[i,2].grid(axis="y")
        # axs[i,2].yaxis.set_ticks(np.arange(0,101,10)) # doesnt make sense for loss as plots get fucked
        legend = axs[i,2].legend(loc='upper right', shadow=True, fontsize='x-large')
    plt.tight_layout()
    fig.savefig(f"{title}.png", dpi=300)
    #plt.show()

In [22]:
for m in models:
    path = f"/home/joking/Downloads/results/deepglobe/{m}/"
    plot_df(path, title=m)

FileNotFoundError: [Errno 2] No such file or directory: '/home/joking/Downloads/results/deepglobe/resnet_base/'

### Sort directories by noise

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np


In [2]:
def sort_dir_by_noise(dir_path):
    top_dir_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
    for a_dir in top_dir_list:
        an = "addnoise"
        an_idx =  a_dir.find(an)
        new_dir = a_dir[an_idx:]
        new_name = a_dir[:an_idx]

        source_dir = os.path.join(dir_path, a_dir)

        target_dir = os.path.join(dir_path, new_dir, new_name)
        try:
            os.makedirs(target_dir)
        except OSError as exc:
            pass


        file_names = os.listdir(source_dir)

        for file_name in file_names:
            shutil.move(os.path.join(source_dir, file_name), target_dir)
        os.rmdir(source_dir)


In [3]:
def collect_results(dir_path,root_dir="", model_name=""):
    
    """
    collect results for a model, assumes the runs are already split for noise level ie
    path is: model/addnoise..subnoise.../time ...
    """
    if not root_dir:
        root_dir = dir_path
    noise_d_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
    results_list = []

    for noise_lvl in noise_d_list:
        model_run_path = os.path.join(dir_path, noise_lvl)
        
        # collect all sub dirs 
        model_run_dirs = [elem for elem in os.listdir(model_run_path) if not elem.startswith('.')]


        for idx, directory in enumerate(model_run_dirs):
            data_list= [model_name]
            index_list = ["Model_Name"]
            # concatenate path
            csv_path = os.path.join(model_run_path, directory, "results.csv")
            tmp_df = pd.read_csv(csv_path, index_col=False)
            
            separate_noise = noise_lvl.split('.')
            for n in separate_noise:
                noise_str,noise_val = n.split('_')
                data_list.append(noise_val)
                index_list.append(noise_str)
                
                
            data_list += directory.split('.')[:-1]
            index_list += ["Time", "dim", 'loss', 'opti', 'lr']

            test_cols= [col for col in tmp_df.columns if col.startswith('test')]
            tmp_df = tmp_df[test_cols]
            last_row = tmp_df.iloc[-1]
            
            final_res= pd.concat([pd.Series(data=data_list, index=index_list)
                                  ,last_row])
            results_list.append(final_res)
        
    df = pd.DataFrame(results_list)
    df.to_csv(f'{root_dir}/{model_name}_results.csv',  na_rep='NULL', index=False) 
    return df

In [48]:
def plot_results(dir_path="/home/joking/Downloads", models = ['resnet', 'lamp', 'cbmlc']):
    losses = ['bce', 'asl', 'weighted_bce']
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    font_size = 27
    n_cols = len(losses)
    n_rows= len(models)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    #axs = axs.flatten()
    fig.suptitle("mAP Score for different Models and Loss Functions", fontsize=font_size, y=1)

    for k, model in enumerate(models):

        model_df = pd.read_csv(f"{dir_path}/{model}_results.csv")
        model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
        model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
        for i, loss in enumerate(losses):
            loss_df = model_df.loc[model_df['loss'] == loss]

            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']*100
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']*100
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']*100

            axs[k,i].plot(ticks, add_noise_df_macro , label='Add Noise - Ma mAP', linestyle='solid', c='r', marker='x')
            axs[k,i].plot(ticks, sub_noise_df_macro , label='Sub Noise - Ma mAP', linestyle='solid', c='b')
            axs[k,i].plot(ticks, mix_noise_df_macro , label='Mix Noise - Ma mAP', linestyle='solid', c='black')
            
            #add_noise_df_micro = loss_df.loc[loss_df['subnoise'] == 0]['test_miAP']*100
            #sub_noise_df_micro = loss_df.loc[loss_df['addnoise'] == 0]['test_miAP']*100
            #mix_noise_df_micro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_miAP']*100

            #axs[k,i].plot(ticks, add_noise_df_micro , label='Add Noise - Micro mAP', linestyle='dashed', c='r')
            #axs[k,i].plot(ticks, sub_noise_df_micro , label='Sub Noise - Micro mAP', linestyle='dashed', c='b')
            #axs[k,i].plot(ticks, mix_noise_df_micro , label='Mix Noise - Micro mAP', linestyle='dashed', c='black')

            axs[k,i].set_title(f'{loss}', fontsize=font_size)
            axs[k,i].set_xlabel('Noise Level')
            axs[k,i].set_ylabel('macro MAP')
            axs[k,i].grid(axis="x")
            axs[k,i].grid(axis="y")
            axs[k,i].yaxis.set_ticks(np.arange(0,101,10))
            legend = axs[k,i].legend(loc='lower left', shadow=True, fontsize='large')



    for ax, row in zip(axs[:,0], models):
        ax.set_ylabel(row, fontsize=font_size)

    plt.tight_layout()
    fig.savefig(f"{dir_path}/final_results.png", dpi=300)
    fig.savefig(f"{dir_path}/final_results.jpg", dpi=300)

    plt.show()   

# Runners

In [49]:
import shutil, os
#################### ############################
models = ['resnet', 'lamp', 'cbmlc']
root_path = "/home/joking/Downloads/results/d50"
for m in models:
    dir_path = f"{root_path}/{m}"

    try:
        # Organize results after noise level
        sort_dir_by_noise(dir_path)

    except OSError:
        pass
    df = collect_results(dir_path, model_name=m, root_dir=root_path)
    
plot_results(dir_path=root_path, models=models)

In [44]:
def calculate_noise_robustness(noise_series):
    # calculate the percentage value how the score is compared to the score without noise
    noise_series = noise_series / noise_series.iloc[0]
    return noise_series

# plot noise robustness
def plot_noise_robustness(root_dir = "", losses=["bce", "asl", "weighted_bce"], models = ['resnet', 'lamp', 'cbmlc']):
    
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]

    n_cols = len(losses)
    n_rows= len(models)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*10 ,n_rows*10), dpi=300)
    #axs = axs.flatten()
    fig.suptitle("Noise Robustness for different Models and Loss Functions", fontsize=18, y=1)
    for k, model in enumerate(models):

        model_df = pd.read_csv(f"{root_dir}/{model}_results.csv")
        model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
        model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
        for i, loss in enumerate(losses):
            loss_df = model_df.loc[model_df['loss'] == loss]

            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']

            add_noise_df_macro = calculate_noise_robustness(add_noise_df_macro)*100
            sub_noise_df_macro = calculate_noise_robustness(sub_noise_df_macro)*100
            mix_noise_df_macro = calculate_noise_robustness(mix_noise_df_macro)*100       
                        
        
            axs[k,i].plot(ticks, add_noise_df_macro , label='Add Noise - Macro mAP', linestyle='solid', c='r')
            axs[k,i].plot(ticks, sub_noise_df_macro , label='Sub Noise - Macro mAP', linestyle='solid', c='b')
            axs[k,i].plot(ticks, mix_noise_df_macro , label='Mix Noise - Macro mAP', linestyle='solid', c='black')
            

            axs[k,i].set_title(f'{loss}', fontsize=18)
            axs[k,i].set_xlabel('Noise Level')
            axs[k,i].set_ylabel('macro MAP')
            axs[k,i].grid(axis="x")
            axs[k,i].grid(axis="y")
            axs[k,i].yaxis.set_ticks(np.arange(0,101,10))
            legend = axs[k,i].legend(loc='lower left', shadow=True, fontsize='large')



    for ax, row in zip(axs[:,0], models):
        ax.set_ylabel(row, fontsize=20)

    plt.tight_layout()
    plt.show()
    fig.savefig(f"{root_dir}/noise_robustness.png", dpi=300)
    fig.savefig(f"{root_dir}/noise_robustness.jpg", dpi=300)


In [45]:
root_path = "/home/joking/Downloads/results/d50"

plot_noise_robustness(root_dir=root_path)

In [116]:
def plot_specific_loss_for_noise_comparison(losses= ["bce", 'asl', 'weighted_bce'], models = ['resnet', 'lamp', 'cbmlc']):
    
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    noises = ['addnoise', 'subnoise', 'mixed']
    n_cols = len(noises)
    n_rows= len(losses)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*10 ,n_rows*10), dpi=300)
    axs = axs.flatten()
    fig.suptitle(f"Each Noisetype compared for each Model for Losses", fontsize=18, y=1)
    

    idx = 0
    for loss in losses:
        # setup the dataframes for each loss
        model_dfs = []
        for model in models:
            model_df = pd.read_csv(f"/home/joking/Downloads/{model}_results.csv")
            model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
            model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
            model_df = model_df.loc[model_df['loss'] == loss]
            model_dfs.append(model_df)
        rn_df = model_dfs[0]
        lamp_df = model_dfs[1]
        cb_df  = model_dfs[2]
        
        #iterate oover noises
        for noise in (noises):

            if noise == 'mixed':
                rn_noise = rn_df.loc[rn_df['addnoise'] == rn_df['subnoise']]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == lamp_df['subnoise']]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == cb_df['subnoise']]['test_maAP']


            elif noise=="subnoise":
                rn_noise = rn_df.loc[rn_df['addnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == 0]['test_maAP']
            else:
                rn_noise = rn_df.loc[rn_df['subnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['subnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['subnoise'] == 0]['test_maAP']




            axs[idx].plot(ticks, rn_noise*100 , label=f'Resnet - Macro mAP', linestyle='solid', c='r')
            axs[idx].plot(ticks, lamp_noise*100 , label=f'Lamp - Macro mAP', linestyle='solid', c='b')
            axs[idx].plot(ticks, cb_noise*100 , label=f' CBMLC- Macro mAP', linestyle='solid', c='black')

            axs[idx].set_title(f'{noise}', fontsize=18)
            axs[idx].set_xlabel('Noise Level')
            axs[idx].set_ylabel('macro MAP')
            axs[idx].grid(axis="x")
            axs[idx].grid(axis="y")
            axs[idx].yaxis.set_ticks(np.arange(0,101,10))
            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='x-large')
            idx += 1
    
    for ax, row in zip(axs[::3], losses):
        ax.set_ylabel(row, fontsize=20)


    plt.tight_layout()
    plt.show()
    fig.savefig(f"/home/joking/Downloads/noise_type_zoomin.png", dpi=300)
    fig.savefig(f"/home/joking/Downloads/noise_type_zoomin.jpg", dpi=300)



In [117]:
plot_specific_loss_for_noise_comparison()